In [10]:
!pip install opencv-python


You should consider upgrading via the '/Users/jeyasri/Documents/WFI-2024/notebook/venv-dataprocessing/bin/python -m pip install --upgrade pip' command.


In [63]:
print(len(os.listdir('/Users/jeyasri/Documents/WFI-2024/MediapipeGestureTraining/FingerGestureDataset/dislike')))
print(len(os.listdir('/Users/jeyasri/Documents/WFI-2024/MediapipeGestureTraining/FingerGestureDataset/mute')))
print(len(os.listdir('/Users/jeyasri/Documents/WFI-2024/MediapipeGestureTraining/FingerGestureDataset/none')))
print(len(os.listdir('/Users/jeyasri/Documents/WFI-2024/MediapipeGestureTraining/FingerGestureDataset/one')))
print(len(os.listdir('/Users/jeyasri/Documents/WFI-2024/MediapipeGestureTraining/FingerGestureDataset/shame')))

1503
1497
1501
1501
1422


In [4]:
import os
#os.sys.path('/Users/jeyasri/anaconda3/lib/python3.8/site-packages')

import sys

sys.path.append('/Users/jeyasri/anaconda3/lib/python3.8/site-packages')

import json
import logging
import random
from tqdm import tqdm
from collections import defaultdict
#from typing import Tuple
#from glob import glob

import pandas as pd
import numpy as np

from PIL import Image, ImageOps
import os
from ipywidgets import interact
from IPython.display import Image as DImage
import cv2
import matplotlib.pyplot as plt

In [ ]:
class TestDataset:
    
    def __init__(self, path_annotation, path_images, is_train, transform=None):
        self.is_train = is_train
        self.transform = transform
        self.path_annotation = path_annotation
        self.path_images = path_images
        self.transform = transform
        self.labels = {label: num for (label, num) in
                       zip(class_names, range(len(class_names)))}
        self.annotations = self.__read_annotations(self.path_annotation)
        
    def get_sample(self, index: int):
        row = self.annotations.iloc[[index]].to_dict('records')[0]
        image_pth = os.path.join(self.path_images, row["target"], row["name"])
        image = Image.open(image_pth).convert("RGB")

        labels = torch.LongTensor([self.labels[label] for label in row["labels"]])

        target = {}
        width, height = image.size

        bboxes = []

        for bbox in row["bboxes"]:
            x1, y1, w, h = bbox
            bbox_abs = [x1 * width, y1 * height, (x1 + w) * width, (y1 + h) * height]
            bboxes.append(bbox_abs)

        target["labels"] = labels
        target["boxes"] = torch.as_tensor(bboxes, dtype=torch.float32)
        target["orig_size"] = torch.as_tensor([int(height), int(width)])

        return image, target

    def __read_annotations(self, path):
        annotations_all = None
        exists_images = []
        for target in class_names:
            path_to_csv = os.path.join(path, f"{target}.json")
            if os.path.exists(path_to_csv):
                json_annotation = json.load(open(
                    os.path.join(path, f"{target}.json")
                ))

                json_annotation = [dict(annotation, **{"name": f"{name}.jpg"}) for name, annotation in
                                   zip(json_annotation, json_annotation.values())]

                annotation = pd.DataFrame(json_annotation)

                annotation["target"] = target
                annotations_all = pd.concat([annotations_all, annotation], ignore_index=True)
                exists_images.extend(
                    self.__get_files_from_dir(os.path.join(self.path_images, target), FORMATS))
            else:
                if target != 'no_gesture':
                    print(f"Database for {target} not found")

        annotations_all["exists"] = annotations_all["name"].isin(exists_images)

        annotations_all = annotations_all[annotations_all["exists"]]

        users = annotations_all["user_id"].unique()
        users = sorted(users)
        random.Random(42).shuffle(users)
        train_users = users[:int(len(users) * 0.8)]
        val_users = users[int(len(users) * 0.8):]

        annotations_all = annotations_all.copy()

        if self.is_train:
            annotations_all = annotations_all[annotations_all["user_id"].isin(train_users)]
        else:
            annotations_all = annotations_all[annotations_all["user_id"].isin(val_users)]

        return annotations_all
    
    def __getitem__(self, index: int):
        image, target = self.get_sample(index)
        if self.transform:
            image = self.transform(image)
        return image, target

In [20]:
!ls data/

dislike      dislike.json mute         mute.json


In [22]:
import json

dislike_file = open('data/dislike.json','r')
dislike_data = json.load(dislike_file)


mute_file = open('data/mute.json','r')
mute_data = json.load(mute_file)

In [25]:
len(dislike_data),len(mute_data)

(100, 100)

In [42]:
mute_data['000b9a1b-d3a5-459f-8326-31235348b807']['bboxes'][0]

[0.48372246, 0.51778145, 0.04780773, 0.10586212]

In [40]:
mute_data['000b9a1b-d3a5-459f-8326-31235348b807']['labels'].index('mute')

0

In [48]:
mute_files = os.listdir('data/mute')

file_index = 1000
for mute_file in mute_files:
    image_pth = 'data/mute/'+mute_file
    image = Image.open(image_pth).convert("RGB")
    mute_prefix = mute_file.split('.')[0]
    mute_index = mute_data[mute_prefix]['labels'].index('mute')
    bbox = mute_data[mute_prefix]['bboxes'][mute_index]  #[0.48372246, 0.51778145, 0.04780773, 0.10586212]
    x1, y1, w, h = bbox
    width, height = image.size

    bbox_abs = [x1 * width, y1 * height, (x1 + w) * width, (y1 + h) * height]
    im1 = image.crop(bbox_abs)
    #im1.show()
    im1 = im1.save("data/mute-processed/"+str(file_index)+".jpg") 
    file_index+=1

    #break


In [49]:
dislike_files = os.listdir('data/dislike')

file_index = 1000
for dislike_file in dislike_files:
    image_pth = 'data/dislike/'+dislike_file
    image = Image.open(image_pth).convert("RGB")
    dislike_prefix = dislike_file.split('.')[0]
    dislike_index = dislike_data[dislike_prefix]['labels'].index('dislike')
    bbox = dislike_data[dislike_prefix]['bboxes'][dislike_index]  #[0.48372246, 0.51778145, 0.04780773, 0.10586212]
    x1, y1, w, h = bbox
    width, height = image.size

    bbox_abs = [x1 * width, y1 * height, (x1 + w) * width, (y1 + h) * height]
    im1 = image.crop(bbox_abs)
    #im1.show()
    #break
    im1 = im1.save("data/dislike-processed/"+str(file_index)+".jpg") 
    file_index+=1

In [34]:
im1 = image.crop(bbox_abs)
im1.show()

im1 = im1.save("data/mute-processed/000b9a1b-d3a5-459f-8326-31235348b807.jpg") 


In [29]:
mute_data['000b9a1b-d3a5-459f-8326-31235348b807']



{'bboxes': [[0.48372246, 0.51778145, 0.04780773, 0.10586212],
  [0.57970344, 0.87207215, 0.04023932, 0.09406977]],
 'labels': ['mute', 'no_gesture'],
 'landmarks': [[[0.49253976997824245, 0.6164478299013858],
   [0.5075014630065252, 0.6056815360704607],
   [0.5142839300748993, 0.5945136527824029],
   [0.5198175526268892, 0.5853628597688285],
   [0.5246561692510847, 0.5759839491842066],
   [0.5018818800328657, 0.5699004656519325],
   [0.5055107567854922, 0.5513342064252238],
   [0.5084483562354524, 0.5373866586148349],
   [0.5104071395477541, 0.5263777980251741],
   [0.4979834769495602, 0.5718403139976568],
   [0.5186588012447548, 0.5707434328943289],
   [0.5208184894912918, 0.5844739653343797],
   [0.5176202352669917, 0.5925035830171913],
   [0.4972704830076016, 0.578720755946446],
   [0.5173709377990758, 0.5835499193732727],
   [0.5164583736359821, 0.5959696900786813],
   [0.5117913227479705, 0.6017000909748633],
   [0.4985609117963489, 0.5875308256856004],
   [0.5138323929596482, 0.5

In [ ]:
transform = T.ToTensor()


class GestureDataset(torch.utils.data.Dataset):

    @staticmethod
    def __get_files_from_dir(pth: str, extns: Tuple):
        if not os.path.exists(pth):
            print(f"Dataset directory doesn't exist {pth}")
            return []
        files = [f for f in os.listdir(pth) if f.endswith(extns)]
        return files

    def __read_annotations(self, path):
        annotations_all = None
        exists_images = []
        for target in class_names:
            path_to_csv = os.path.join(path, f"{target}.json")
            if os.path.exists(path_to_csv):
                json_annotation = json.load(open(
                    os.path.join(path, f"{target}.json")
                ))

                json_annotation = [dict(annotation, **{"name": f"{name}.jpg"}) for name, annotation in
                                   zip(json_annotation, json_annotation.values())]

                annotation = pd.DataFrame(json_annotation)

                annotation["target"] = target
                annotations_all = pd.concat([annotations_all, annotation], ignore_index=True)
                exists_images.extend(
                    self.__get_files_from_dir(os.path.join(self.path_images, target), FORMATS))
            else:
                if target != 'no_gesture':
                    print(f"Database for {target} not found")

        annotations_all["exists"] = annotations_all["name"].isin(exists_images)

        annotations_all = annotations_all[annotations_all["exists"]]

        users = annotations_all["user_id"].unique()
        users = sorted(users)
        random.Random(42).shuffle(users)
        train_users = users[:int(len(users) * 0.8)]
        val_users = users[int(len(users) * 0.8):]

        annotations_all = annotations_all.copy()

        if self.is_train:
            annotations_all = annotations_all[annotations_all["user_id"].isin(train_users)]
        else:
            annotations_all = annotations_all[annotations_all["user_id"].isin(val_users)]

        return annotations_all

    def __init__(self, path_annotation, path_images, is_train, transform=None):
        self.is_train = is_train
        self.transform = transform
        self.path_annotation = path_annotation
        self.path_images = path_images
        self.transform = transform
        self.labels = {label: num for (label, num) in
                       zip(class_names, range(len(class_names)))}
        self.annotations = self.__read_annotations(self.path_annotation)

    def __len__(self):
        return self.annotations.shape[0]

    def get_sample(self, index: int):
        row = self.annotations.iloc[[index]].to_dict('records')[0]
        image_pth = os.path.join(self.path_images, row["target"], row["name"])
        image = Image.open(image_pth).convert("RGB")

        labels = torch.LongTensor([self.labels[label] for label in row["labels"]])

        target = {}
        width, height = image.size

        bboxes = []

        for bbox in row["bboxes"]:
            x1, y1, w, h = bbox
            bbox_abs = [x1 * width, y1 * height, (x1 + w) * width, (y1 + h) * height]
            bboxes.append(bbox_abs)

        target["labels"] = labels
        target["boxes"] = torch.as_tensor(bboxes, dtype=torch.float32)
        target["orig_size"] = torch.as_tensor([int(height), int(width)])

        return image, target

    def __getitem__(self, index: int):
        image, target = self.get_sample(index)
        if self.transform:
            image = self.transform(image)
        return image, target

In [1]:
import pandas as pd
# ref: https://www.kaggle.com/datasets/innominate817/hagrid-sample-30k-384p/code

In [2]:
dislike_path = '/Users/jeyasri/Documents/WFI-2024/notebook/data/dislike/'

dislike_path2 = '/Users/jeyasri/Downloads/hagrid-sample-30k-384p/hagrid_30k/train_val_dislike/'

dislike_annotation_path = '/Users/jeyasri/Downloads/hagrid-sample-30k-384p/ann_train_val/dislike.json'

mute_path = '/Users/jeyasri/Downloads/hagrid-sample-30k-384p/hagrid_30k/train_val_mute/'

mute_annotation_path = '/Users/jeyasri/Downloads/hagrid-sample-30k-384p/ann_train_val/mute.json'


mute_path2 = '/Users/jeyasri/Documents/WFI-2024/notebook/data/mute/'


one_path = '/Users/jeyasri/Downloads/hagrid-sample-30k-384p/hagrid_30k/train_val_one/'

one_annotation_path = '/Users/jeyasri/Downloads/hagrid-sample-30k-384p/ann_train_val/one.json'


In [1]:
!ls /Users/jeyasri/Downloads/hagrid-sample-30k-384p/hagrid_30k/

train_val_call            train_val_ok              train_val_stop
train_val_dislike         train_val_one             train_val_stop_inverted
train_val_fist            train_val_palm            train_val_three
train_val_four            train_val_peace           train_val_three2
train_val_like            train_val_peace_inverted  train_val_two_up
train_val_mute            train_val_rock            train_val_two_up_inverted


In [2]:
!ls /Users/jeyasri/Downloads/hagrid-sample-30k-384p/ann_train_val/

call.json            ok.json              stop.json
dislike.json         one.json             stop_inverted.json
fist.json            palm.json            three.json
four.json            peace.json           three2.json
like.json            peace_inverted.json  two_up.json
mute.json            rock.json            two_up_inverted.json


In [7]:
dislike_df = pd.read_json(dislike_annotation_path).transpose()
print(dislike_df.shape)
dislike_df.head()

(28537, 5)


bboxes  \
001c6f56-85cf-4e45-bfc1-1af53c0e501b  [[0.29848959, 0.56869285, 0.07580751000000001,...   
002b80a7-3292-4202-9a25-d6c8aac83a1e  [[0.29465646, 0.84238796, 0.15554635, 0.095810...   
002df411-ccd1-4949-8540-11683821faa3  [[0.3012859, 0.20967595, 0.10979249, 0.1221433...   
002e5485-87dd-4b79-a9ef-c6a1d723e67b  [[0.23585067, 0.67519586, 0.06739478, 0.089843...   
00481821-8795-4011-bc0a-67f99fa53cac  [[0.44343412, 0.1741347, 0.04166024, 0.1322412...   

                                                     labels leading_hand  \
001c6f56-85cf-4e45-bfc1-1af53c0e501b  [no_gesture, dislike]         left   
002b80a7-3292-4202-9a25-d6c8aac83a1e  [no_gesture, dislike]         left   
002df411-ccd1-4949-8540-11683821faa3  [dislike, no_gesture]        right   
002e5485-87dd-4b79-a9ef-c6a1d723e67b  [no_gesture, dislike]         left   
00481821-8795-4011-bc0a-67f99fa53cac  [dislike, no_gesture]        right   

                                     leading_conf  \
001c6f56-85cf-4e45-bfc1-1af53c0e501b            1   
002b80a7-3292-4202-9a25-d6c8aac83a1e            1   
002df411-ccd1-4949-8540-11683821faa3            1   
002e5485-87dd-4b79-a9ef-c6a1d723e67b            1   
00481821-8795-4011-bc0a-67f99fa53cac            1   

                                                                                user_id  
001c6f56-85cf-4e45-bfc1-1af53c0e501b  7c1d5778e9e3b4545386bed18a31ed20c7d32e18c90d29...  
002b80a7-3292-4202-9a25-d6c8aac83a1e  2764ab11a5e84e7a9336d238aa8677f8bb9ae3d9f41516...  
002df411-ccd1-4949-8540-11683821faa3  4f9ef9eaac1d0052e58593e0977f1667e88642e8862394...  
002e5485-87dd-4b79-a9ef-c6a1d723e67b  80db57eca3a1a985c4e994d023c49b7cd3ed38ebdea79a...  
00481821-8795-4011-bc0a-67f99fa53cac  216bf9c35128c80c7016aef76c6eb3c82f9cd50dfda0aa...

In [11]:
mute_df = pd.read_json(mute_annotation_path).transpose()
print(mute_df.shape)
mute_df.head()

(28971, 5)


bboxes  \
000b9a1b-d3a5-459f-8326-31235348b807  [[0.48372246, 0.51778145, 0.04780773, 0.105862...   
000d3f03-ca4b-44cc-8d8c-cdd12735e35b  [[0.30495339, 0.5748133400000001, 0.52472458, ...   
0018e992-f88e-4dd3-89c4-83d933e6b063  [[0.50047942, 0.61563948, 0.11658545000000001,...   
00283157-0fa8-4931-9ec1-a85ed9feac9b  [[0.43165491, 0.28045531, 0.03996719, 0.113830...   
002b2e3b-9d21-4921-a418-8435bc65fa59  [[0.44529762, 0.24427071, 0.1457059, 0.2161295...   

                                                  labels leading_hand  \
000b9a1b-d3a5-459f-8326-31235348b807  [mute, no_gesture]        right   
000d3f03-ca4b-44cc-8d8c-cdd12735e35b              [mute]        right   
0018e992-f88e-4dd3-89c4-83d933e6b063              [mute]        right   
00283157-0fa8-4931-9ec1-a85ed9feac9b  [mute, no_gesture]        right   
002b2e3b-9d21-4921-a418-8435bc65fa59  [mute, no_gesture]        right   

                                     leading_conf  \
000b9a1b-d3a5-459f-8326-31235348b807            1   
000d3f03-ca4b-44cc-8d8c-cdd12735e35b            1   
0018e992-f88e-4dd3-89c4-83d933e6b063            1   
00283157-0fa8-4931-9ec1-a85ed9feac9b            1   
002b2e3b-9d21-4921-a418-8435bc65fa59            1   

                                                                                user_id  
000b9a1b-d3a5-459f-8326-31235348b807  77443178788d7a05ba0af7dc78167163a9ddda68c09658...  
000d3f03-ca4b-44cc-8d8c-cdd12735e35b  5beb90cf59482df367e1d4f9ab93518e7be4f8c63a50f5...  
0018e992-f88e-4dd3-89c4-83d933e6b063  c1b59340bc23985bd32c4a268bee5ff8d70c75b434f76a...  
00283157-0fa8-4931-9ec1-a85ed9feac9b  f880d44910f866441905ad78e8b61a15cdfd06552f8989...  
002b2e3b-9d21-4921-a418-8435bc65fa59  fb038674dc76f3bea11a051dabde0df08582bfdd3a8ad9...

In [5]:
one_df = pd.read_json(one_annotation_path).transpose()
print(one_df.shape)
one_df.head()

(28444, 5)


bboxes  \
002ce59b-be3f-4002-b2fe-367f84e2e3a4  [[0.10821009000000001, 0.26112599000000003, 0....   
004c317a-ec98-41da-982a-e1ba5de685e8  [[0.6825672500000001, 0.16698166, 0.08854563, ...   
005e49fa-e567-4bd9-a49d-ee0cfe1b6ed0  [[0.5546385500000001, 0.42332198, 0.10369781, ...   
00b52e12-04b4-4c77-a4c6-923a46a7578c  [[0.36863281000000003, 0.36358745000000003, 0....   
00b5f431-5da9-4684-8b22-e2ca85d299f0  [[0.29783729999999997, 0.17928394, 0.22665508,...   

                                                 labels leading_hand  \
002ce59b-be3f-4002-b2fe-367f84e2e3a4  [one, no_gesture]        right   
004c317a-ec98-41da-982a-e1ba5de685e8              [one]         left   
005e49fa-e567-4bd9-a49d-ee0cfe1b6ed0              [one]         left   
00b52e12-04b4-4c77-a4c6-923a46a7578c  [one, no_gesture]        right   
00b5f431-5da9-4684-8b22-e2ca85d299f0  [no_gesture, one]         left   

                                     leading_conf  \
002ce59b-be3f-4002-b2fe-367f84e2e3a4            1   
004c317a-ec98-41da-982a-e1ba5de685e8            1   
005e49fa-e567-4bd9-a49d-ee0cfe1b6ed0            1   
00b52e12-04b4-4c77-a4c6-923a46a7578c            1   
00b5f431-5da9-4684-8b22-e2ca85d299f0          0.6   

                                                                                user_id  
002ce59b-be3f-4002-b2fe-367f84e2e3a4  d02be2d50b25cec5cbcc9f9f56b0e154647e2a17fa16a3...  
004c317a-ec98-41da-982a-e1ba5de685e8  d5a529ce9f2d28463bfb8dbc6b9669a7cc347f6ed59b09...  
005e49fa-e567-4bd9-a49d-ee0cfe1b6ed0  6b32f0a26f413a006387f49ceeeaf8610ab2fbcabe3378...  
00b52e12-04b4-4c77-a4c6-923a46a7578c  ed83cdc35863398839b11886e1ee1ad685c6f53580c6d8...  
00b5f431-5da9-4684-8b22-e2ca85d299f0  8b1d9fb8a96a8d208ba2dcdaadf0aec5a4903e7fb209e9...

In [44]:
dislike_file = open(dislike_annotation_path,'r')
dislike_data = json.load(dislike_file)
mute_file = open(mute_annotation_path,'r')
mute_data = json.load(mute_file)

<function dict.keys>

In [31]:
file_index = 2000

for i ,row in dislike_data.iterrows():
    print('i ',i,'  row[0]', row[0])
    image_pth = dislike_path+i+'.jpg'
    if not os.path.exists(image_pth):
        image_pth = dislike_path2+i+'.jpg'
    if not os.path.exists(dislike_path2+i+'.jpg'): 
        continue
    image = Image.open(image_pth).convert("RGB")
    dislike_prefix = i #dislike_file.split('.')[0]
    dislike_index = row[1].index('dislike')
    bbox = row[0][dislike_index]  #[0.48372246, 0.51778145, 0.04780773, 0.10586212]
    x1, y1, w, h = bbox
    width, height = image.size
    bbox_abs = [x1 * width, y1 * height, (x1 + w) * width, (y1 + h) * height]
    im1 = image.crop(bbox_abs)
    #im1.show()
    im1 = im1.save("data/dislike-processed/"+str(file_index)+".jpg") 
    file_index+=1
    #break

i  001c6f56-85cf-4e45-bfc1-1af53c0e501b   row[0] [[0.29848959, 0.56869285, 0.07580751000000001, 0.06830282], [0.47884104, 0.3353942, 0.08987013, 0.09639664]]
i  002b80a7-3292-4202-9a25-d6c8aac83a1e   row[0] [[0.29465646, 0.84238796, 0.15554635, 0.09581099], [0.47209969, 0.48938827, 0.14441872, 0.10660058]]
i  002df411-ccd1-4949-8540-11683821faa3   row[0] [[0.3012859, 0.20967595, 0.10979249, 0.12214336], [0.66215607, 0.7327155, 0.1026638, 0.13769088000000002]]
i  002e5485-87dd-4b79-a9ef-c6a1d723e67b   row[0] [[0.23585067, 0.67519586, 0.06739478, 0.08984303], [0.49861325, 0.26719229, 0.08662546, 0.09429372]]
i  00481821-8795-4011-bc0a-67f99fa53cac   row[0] [[0.44343412, 0.1741347, 0.04166024, 0.13224127], [0.5647830500000001, 0.57104644, 0.03492798, 0.10973228]]
i  00713c1a-007e-4651-bef5-09c4019f19c6   row[0] [[0.46864302, 0.42210965, 0.0878205, 0.07382369999999999], [0.53766225, 0.64271497, 0.0772895, 0.048004450000000004]]
i  00a5bf41-da88-49cd-88b5-b7d0a4e6158f   row[0] [[0.318533380

i  04d83ce8-93af-4f57-a031-48a05a931b71   row[0] [[0.25473296, 0.83715008, 0.07123812, 0.12590541], [0.59648433, 0.39186598, 0.08521748, 0.08965461]]
i  04dc1bce-6a52-437d-821f-cf87eca59f13   row[0] [[0.35044863, 0.43527044000000004, 0.13007452, 0.15635239]]
i  04e82298-d2e3-4944-a6d5-67c4eefc4a80   row[0] [[0.54258916, 0.26964268, 0.057091899999999994, 0.0658496], [0.68839538, 0.50581229, 0.05641599, 0.04895949]]
i  04ea9e7b-7596-422b-b965-83db0b2c8059   row[0] [[0.47314712000000003, 0.4632675, 0.14620298, 0.13648052]]
i  04f93a8c-88d2-4666-882a-b65dac282aef   row[0] [[0.28968659999999996, 0.30823625, 0.10883803, 0.12573769], [0.6780408, 0.75282635, 0.09752471, 0.11234518]]
i  04fef263-5790-4e61-936b-64de8de07ac6   row[0] [[0.33430911, 0.47821956, 0.05377109, 0.05238603], [0.43348964, 0.64411215, 0.05936393, 0.031244380000000002]]
i  05037a97-c299-434a-b31a-06ca099ac1f7   row[0] [[0.54651316, 0.41419314, 0.10699709, 0.1692073], [0.85094088, 0.79408482, 0.14490245000000002, 0.13652041]

i  0db85c05-b2fd-43fa-b33e-d1142def79e1   row[0] [[0.28503943, 0.73290772, 0.09122057, 0.07761363]]
i  0dc4792c-dbfe-4ca4-be3c-2688e7fb48ef   row[0] [[0.24118599000000002, 0.53441005, 0.23989912, 0.14776604000000002]]
i  0dc5b2a5-682f-4720-9fe0-c29864514e2e   row[0] [[0.53412399, 0.16801638, 0.15832359000000001, 0.16143508]]
i  0dda94f7-317f-4f47-ac9c-44e7a809781f   row[0] [[0.42991298, 0.32784382, 0.062472810000000004, 0.06384615], [0.57812368, 0.52043001, 0.051061220000000004, 0.03856594]]
i  0de52658-f436-4d1b-aacd-b853d61dca0c   row[0] [[0.64034591, 0.71350723, 0.052914199999999995, 0.12411965]]
i  0de541ef-b573-446c-9c37-fa8c35087ae5   row[0] [[0.18336723, 0.78106028, 0.10643391, 0.11469777], [0.5631648300000001, 0.37900316, 0.09507861000000001, 0.10035385000000001]]
i  0dedbfa7-1767-4cbf-b82f-1f2452532eaf   row[0] [[0.31024125, 0.78101267, 0.06860436, 0.08634169], [0.5631191600000001, 0.37277619, 0.08605146, 0.09817009]]
i  0dee1f07-04cc-4001-93a0-5456110bf6d7   row[0] [[0.336467

i  1ed9c80f-998d-4a8c-9093-5606d450eb25   row[0] [[0.26988889, 0.6154376500000001, 0.10720943000000001, 0.11413132000000001]]
i  1eeb28c8-101c-471e-955c-733e4030a1bb   row[0] [[0.54387487, 0.77371585, 0.04190728, 0.059128520000000004], [0.70248495, 0.5258376300000001, 0.06481794, 0.061741290000000004]]
i  1ef90ce6-f873-43df-82c4-13eac3d47793   row[0] [[0.59308357, 0.27124087, 0.06936058, 0.13605834]]
i  1efb1566-db42-4701-b952-de778143c526   row[0] [[0.39734374, 0.32415279, 0.05633628, 0.17379883000000002]]
i  1f0462ed-ae5e-4dae-8921-e3a53921a6d5   row[0] [[0.21930386000000002, 0.73850415, 0.06966985, 0.09293863000000001], [0.53980688, 0.39952428, 0.08090872, 0.09314296]]
i  1f159400-b6a7-4023-bf9c-3e032d890010   row[0] [[0.32787334, 0.15312146000000001, 0.12623589, 0.16057216]]
i  1f41c52d-49b0-4124-99e5-71ed03e43055   row[0] [[0.26285667, 0.5822875, 0.18326361, 0.25678729]]
i  1f7759f0-68ee-47bd-b49b-aa0c4097a480   row[0] [[0.46038172, 0.407655, 0.10511891, 0.24533375000000002]]
i  1

i  30d2de79-1b97-456d-9c32-99b70706517d   row[0] [[0.31809161, 0.75727904, 0.06643098, 0.11682552], [0.45850794, 0.4307988, 0.09151133, 0.10078948]]
i  30d60e0c-3583-4dfb-8796-3a6aaf749b4d   row[0] [[0.30603807, 0.06419478, 0.11789753, 0.16392377], [0.7509944, 0.55880263, 0.08710931, 0.10658873]]
i  30d69450-3ba5-489d-ba4f-21be0ac69452   row[0] [[0.54922683, 0.44173602, 0.03323093, 0.02930971], [0.65424919, 0.28559973, 0.03785744, 0.03646953]]
i  3117fa86-121b-4812-9783-ff9570da9dd2   row[0] [[0.46999901, 0.25207979, 0.15531655, 0.13835008000000001]]
i  3118a405-1fbb-4ef8-8f80-52946e7ef5fe   row[0] [[0.32677392, 0.40054145, 0.08574412000000001, 0.10531837000000001], [0.73837207, 0.85736888, 0.08349986, 0.13870956]]
i  311dc3ff-a10c-4977-aa1c-eb7f8fcd52d8   row[0] [[0.43628951, 0.49340222, 0.07988271, 0.08438647]]
i  31208463-7e07-473c-9fdb-4b01e6e4db5a   row[0] [[0.08877833, 0.29845833, 0.336175, 0.39876000000000006]]
i  31267cf1-9b0b-4767-b873-a98f46324b07   row[0] [[0.43706798, 0.278

...

i  e4bea106-ed8e-47b5-a422-b1f70a0b26b9   row[0] [[0.43905696, 0.58478086, 0.06383863000000001, 0.12459907]]
i  e4d67cb0-2bc5-49c8-8c8c-a2e3457d7eb4   row[0] [[0.49763166000000003, 0.69009103, 0.04020191, 0.07537929]]
i  e4e25d9d-0b3a-44e3-8a96-b220b05370aa   row[0] [[0.38645431, 0.43686817, 0.08760478000000001, 0.23535844]]
i  e4e270c6-9b90-423a-80a6-247b88f63dc6   row[0] [[0.48783004, 0.31063863, 0.10210515, 0.18432578]]
i  e4e70af3-0444-47ce-9bdd-f7b67d8fb616   row[0] [[0.19353163, 0.36721935, 0.22585614, 0.22059967]]
i  e4e7e1b1-b5ab-4b0c-b0df-5c6494ebf186   row[0] [[0.34167935, 0.27227424, 0.10568403, 0.09797955]]
i  e4e86659-247a-4f86-8378-b099550088ac   row[0] [[0.43053824, 0.45346679, 0.12547494, 0.1287699]]
i  e4ea0bd8-28ba-49d6-bea7-f02486eab95f   row[0] [[0.29792816, 0.40966529999999995, 0.16848563, 0.19407068]]
i  e4f784d6-3030-47ad-a009-2f400c73a276   row[0] [[0.58708301, 0.47129324, 0.10469234000000001, 0.19480109]]
i  e5000c88-9d6e-401f-8b21-c92f95c769ce   row[0] [[0.095

i  ec142334-3708-4b86-a1e6-435ddf74e68c   row[0] [[0.44312106, 0.23126054000000001, 0.10620213, 0.22801701]]
i  ec14db9b-2658-4ff3-92d3-024a444cefc1   row[0] [[0.33445641, 0.45672514000000003, 0.08587398, 0.09858289]]
i  ec152c84-85e3-41bc-a748-c516e6d20815   row[0] [[0.65959451, 0.25830505, 0.07894665000000001, 0.07453021]]
i  ec16c92f-22ce-4592-86a4-44e89a198fd2   row[0] [[0.58243365, 0.48958145000000003, 0.28768559, 0.27323193]]
i  ec178b48-58f5-4dbc-9beb-45d5da81ccac   row[0] [[0.51898696, 0.34583528, 0.13841979000000001, 0.10931043]]
i  ec1820f3-e014-428a-87af-84563a737eb1   row[0] [[0.18051935, 0.78980955, 0.08402703, 0.13305829], [0.4495344, 0.34415232, 0.12001124, 0.13243277]]
i  ec20cc0f-669e-4154-9ee5-dd9828c98689   row[0] [[0.2692098, 0.6150056700000001, 0.12264782, 0.14585112]]
i  ec2522be-3567-440b-8ad6-d224505b4b25   row[0] [[0.54626756, 0.45021033, 0.13959013, 0.13845344]]
i  ec2b2ea3-3e8e-49bd-93c2-a8ccf240c806   row[0] [[0.60121819, 0.25986753, 0.11498935, 0.21987797]]

i  f1a390a8-f57f-431a-bdcc-c060a75ed84e   row[0] [[0.5568671, 0.32499412, 0.16333555, 0.15399225]]
i  f1ab3d9b-9c47-44e8-bc58-367ae73bb670   row[0] [[0.41836048000000003, 0.63395141, 0.07151613, 0.14818141]]
i  f1af85ce-155c-46c4-b8dc-9e72a0604e12   row[0] [[0.47109754000000004, 0.34777596, 0.09692018000000001, 0.11198383]]
i  f1b0212d-8f4b-45c2-adda-1a2316f3bf8a   row[0] [[0.25663082, 0.49246648, 0.16324493, 0.16800882]]
i  f1b8eeaa-a614-4396-a799-f12f485697ce   row[0] [[0.15486561000000001, 0.43763349999999995, 0.17939823, 0.16683632]]
i  f1bd3736-f9e6-4213-b220-60d157a2ab06   row[0] [[0.51385952, 0.13345956, 0.14405484, 0.16292071]]
i  f1bd7047-9774-4628-a21a-92f8023797a5   row[0] [[0.66568764, 0.298573, 0.20929962, 0.1582007]]
i  f1beb0fd-c28e-465e-817f-b71b61330a89   row[0] [[0.42267798, 0.33082272, 0.14838417, 0.13348206]]
i  f1c16083-f4a7-4a11-8826-6cabee057310   row[0] [[0.5494493, 0.6846599, 0.03976792, 0.07479998]]
i  f1c55f62-27b4-40da-adce-138cf2f198ab   row[0] [[0.4954319,

i  f6bd2c67-22b0-4c4c-bc92-4183b7b2e960   row[0] [[0.40826809000000003, 0.29359274, 0.12583029, 0.13343506]]
i  f6bda014-fc52-4746-825c-d44ff5c09b24   row[0] [[0.43108349, 0.28793084, 0.11063063000000001, 0.11590809]]
i  f6c141d8-7e39-4134-beab-b1d781f8f749   row[0] [[0.3808736, 0.58795728, 0.08989201000000001, 0.07441247000000001]]
i  f6c43e5f-b462-4916-aeff-5c0685bacb52   row[0] [[0.31312404, 0.30386442, 0.09717098, 0.18209385]]
i  f6c680df-6e84-45de-85be-465e28bd54ca   row[0] [[0.45307021000000003, 0.26821253, 0.10705575, 0.21789072]]
i  f6dead02-5957-46a0-abf4-bfbc253f729c   row[0] [[0.36419688, 0.44608691, 0.10460336, 0.11100659]]
i  f6e558dd-18b4-4b60-8e7a-f9af1e99bfa0   row[0] [[0.38376762000000003, 0.74389005, 0.15720923, 0.17400804]]
i  f6ea8e96-1eba-4b4d-98f4-9f326e6c006c   row[0] [[0.32973352, 0.48283466, 0.03519791, 0.0342047]]
i  f6eefcd1-43ed-4f83-99c7-611fd85ee493   row[0] [[0.47235097000000004, 0.39811344, 0.20640733, 0.21238477]]
i  f6f39464-35cc-40f7-832c-b4ddd942744b

i  fcfc9954-fcea-4fb8-889a-ce178169643a   row[0] [[0.51791533, 0.5554285, 0.19107354000000001, 0.13481474000000002]]
i  fd01aaea-ab74-499f-8582-887c87f51333   row[0] [[0.36792642000000003, 0.48278546, 0.17598061, 0.19076488]]
i  fd0475db-1a85-4515-bab1-f96518a2bcb4   row[0] [[0.19137157, 0.61322779, 0.08785359, 0.11761138], [0.3857622, 0.21275106, 0.12777766000000002, 0.11639172]]
i  fd07db6e-2c39-4b4e-92ab-9ff8cb478c72   row[0] [[0.26856272000000003, 0.65297406, 0.13333912, 0.13956855]]
i  fd0c7660-d9b5-467d-b9ee-d483f0708b1d   row[0] [[0.3725177, 0.4189153, 0.13753397, 0.13630913]]
i  fd13c45a-95c8-47cd-a78b-09ba37a16d7f   row[0] [[0.35392564, 0.51227433, 0.09802259, 0.21829668]]
i  fd23a7e4-0180-472c-8dc9-243edea68439   row[0] [[0.47549941, 0.44047538, 0.11565157000000001, 0.11923976]]
i  fd368c11-9208-4363-b2d8-4ce8e341c7ac   row[0] [[0.22587463, 0.38363423, 0.14190122, 0.16272278]]
i  fd3ebd14-da65-4da4-9b7a-76c8698fb895   row[0] [[0.54491246, 0.43249888000000003, 0.12503834, 0.13

In [28]:
!ls data/

dislike           dislike.json      mute-processed
dislike-processed mute              mute.json


In [35]:
#os.path.exists('')

for folder in os.listdir('/Users/jeyasri/Downloads/hagrid-sample-30k-384p/hagrid_30k/'):
    print(folder,' - ',os.path.exists('/Users/jeyasri/Downloads/hagrid-sample-30k-384p/hagrid_30k/'+folder+'3f3eed89-591e-469a-bef5-4c4041e06d8d.jpg'))

train_val_two_up  -  False
train_val_rock  -  False
train_val_peace  -  False
.DS_Store  -  False
train_val_two_up_inverted  -  False
train_val_ok  -  False
train_val_call  -  False
train_val_fist  -  False
train_val_palm  -  False
train_val_four  -  False
train_val_peace_inverted  -  False
train_val_stop_inverted  -  False
train_val_dislike  -  False
train_val_one  -  False
train_val_like  -  False
train_val_stop  -  False
train_val_three2  -  False
train_val_mute  -  False
train_val_three  -  False


In [33]:
file_index = 3000

for i ,row in mute_data.iterrows():
    print('i ',i,'  row[0]', row[0])
    image_pth = mute_path+i+'.jpg'
    if not os.path.exists(image_pth):
        image_pth = mute_path2+i+'.jpg'
    if not os.path.exists(mute_path2+i+'.jpg'): 
        continue
    image = Image.open(image_pth).convert("RGB")
    mute_prefix = i #dislike_file.split('.')[0]
    mute_index = row[1].index('mute')
    bbox = row[0][mute_index]  #[0.48372246, 0.51778145, 0.04780773, 0.10586212]
    x1, y1, w, h = bbox
    width, height = image.size
    bbox_abs = [x1 * width, y1 * height, (x1 + w) * width, (y1 + h) * height]
    im1 = image.crop(bbox_abs)
    #im1.show()
    im1 = im1.save("data/mute-processed/"+str(file_index)+".jpg") 
    file_index+=1
    #break

i  000b9a1b-d3a5-459f-8326-31235348b807   row[0] [[0.48372246, 0.51778145, 0.04780773, 0.10586212], [0.57970344, 0.87207215, 0.04023932, 0.09406977]]
i  000d3f03-ca4b-44cc-8d8c-cdd12735e35b   row[0] [[0.30495339, 0.5748133400000001, 0.52472458, 0.40485008]]
i  0018e992-f88e-4dd3-89c4-83d933e6b063   row[0] [[0.50047942, 0.61563948, 0.11658545000000001, 0.15381207]]
i  00283157-0fa8-4931-9ec1-a85ed9feac9b   row[0] [[0.43165491, 0.28045531, 0.03996719, 0.11383058], [0.5165756, 0.68412187, 0.03426013, 0.09778769]]
i  002b2e3b-9d21-4921-a418-8435bc65fa59   row[0] [[0.44529762, 0.24427071, 0.1457059, 0.2161295], [0.82127502, 0.85311459, 0.17027579, 0.08650578]]
i  002f3c49-9d32-48dc-a43c-ea558bd7a662   row[0] [[0.47840157, 0.3522046, 0.03902718, 0.05323352], [0.55084867, 0.51586072, 0.03594418, 0.040352]]
i  00301ce6-2aed-4fc8-8fe3-e01e0ac037ce   row[0] [[0.54109833, 0.69113315, 0.07529851, 0.09833629]]
i  0037d2aa-e6e5-4e55-bb6a-6c8a4418e628   row[0] [[0.34567019, 0.52677152, 0.27402815, 0.

i  0436ed1c-5ec1-4cc1-9b6c-7e5bac197c59   row[0] [[0.48336706, 0.25241968, 0.09560135, 0.20264442]]
i  0438a9b0-9ef0-4497-9117-818c8e1c7cc8   row[0] [[0.29752333000000003, 0.55586167, 0.40899167000000003, 0.43930667]]
i  043b71d1-0895-48dd-b2a6-78ac69fd90b9   row[0] [[0.43364381, 0.36665984, 0.15244222, 0.16768329]]
i  044a44d4-7cfb-4d15-8d5e-59a5e94dab8a   row[0] [[0.49565361, 0.20390787, 0.10871108, 0.13471087], [0.72832316, 0.68634328, 0.09024672, 0.13758922]]
i  045a40cb-da37-4f3b-8121-2e964633e6e1   row[0] [[0.41149667, 0.47770833, 0.42464167, 0.50429167]]
i  04715f5a-6810-43f1-b1a4-782698244230   row[0] [[0.36098483000000003, 0.60851717, 0.44809989, 0.38939116]]
i  04745c30-505a-4a1e-be71-f97b6ea335f5   row[0] [[0.35788167, 0.71757167, 0.28361000000000003, 0.27786167]]
i  04792259-3032-4ebb-a2ab-ef47a5da766e   row[0] [[0.44817409, 0.74269932, 0.11389679999999999, 0.12692433]]
i  047c23a6-7939-4d17-9c1a-3efd73123c82   row[0] [[0.35383892, 0.5915505999999999, 0.31062, 0.39925167]]


i  20450f90-a81d-4c78-a303-c24130db87f9   row[0] [[0.37639983, 0.54654661, 0.23569218, 0.27724489999999996]]
i  20522403-d06f-41b3-90bb-9a0d936d026c   row[0] [[0.24380525, 0.52705528, 0.36645599, 0.46771139]]
i  20647bb2-1e26-4a64-8ac0-08c5956e0ca0   row[0] [[0.39074076, 0.30002216, 0.11833926, 0.14884018000000002], [0.66019815, 0.8753218500000001, 0.11436661000000001, 0.12453149000000001]]
i  2088edfd-d216-4b9d-9b81-c7a3e50b5cb6   row[0] [[0.47807107, 0.41879027, 0.09466692, 0.23818565]]
i  208b5698-79f6-47b5-8968-b267fa697784   row[0] [[0.42588081, 0.42657963, 0.10089805, 0.24561722], [0.52693995, 0.8124732, 0.11724619, 0.182038]]
i  20b07903-5b57-4c9f-a667-9943c483a19e   row[0] [[0.37227498000000003, 0.26226363, 0.06506686, 0.08869134000000001], [0.50819653, 0.54538545, 0.05865949, 0.07723031]]
i  20b7ba18-6b2e-47bf-a96b-0a3eda3f52f0   row[0] [[0.35931799000000003, 0.44006621, 0.28918213, 0.36704909]]
i  20b95ded-1e6b-4016-a9a0-1b3d43a0dcd7   row[0] [[0.24324735, 0.7320455, 0.094312

i  304daf0d-746a-47ce-99e3-8c9c093995cf   row[0] [[0.41775452, 0.57795347, 0.12576299, 0.14921433]]
i  306de50a-6453-4a60-a7fd-62d9213b28f9   row[0] [[0.33644586, 0.50880788, 0.29182109, 0.38377867]]
i  306ed3bc-27d3-4e15-aa6c-3416e06eb4a0   row[0] [[0.35303402, 0.45392000000000005, 0.06529965, 0.11972709000000001], [0.46470017, 0.80401381, 0.05222616, 0.11320922]]
i  30746ea7-27aa-47d1-a82b-afe9589dfba4   row[0] [[0.33848375, 0.267165, 0.211165, 0.33953000000000005]]
i  30778e0f-2151-49ea-90b6-614b7c813636   row[0] [[0.39631355, 0.31801083, 0.15066275, 0.17553717]]
i  30badaa3-b127-464e-a766-90959b2f33a6   row[0] [[0.39443878, 0.91482493, 0.13556118, 0.08500507], [0.43493527, 0.26799128, 0.09471333, 0.2025275]]
i  30ef7c07-3f01-4191-9b99-efcc4289e690   row[0] [[0.39546000000000003, 0.45127167, 0.19125499999999998, 0.53076833]]
i  30f92572-fb0d-4755-9a18-2b676cea9dfc   row[0] [[0.41616667, 0.43834667, 0.30480167, 0.5065649999999999]]
i  3105d912-8ffa-478c-b03a-32f191bfe04c   row[0] [[0

i  42c56345-6f69-40ef-bcae-9918a4a96c90   row[0] [[0.41083496, 0.39432558, 0.21585038, 0.27029701]]
i  42d15f42-0531-4b49-a15f-c5d01bf6bb46   row[0] [[0.4414661, 0.60887423, 0.060290830000000004, 0.06998486], [0.60435676, 0.87938847, 0.06359634, 0.08795025000000001]]
i  4305150b-75a7-4ef7-9242-01e38ab74b1f   row[0] [[0.5298642100000001, 0.43880046, 0.05609017, 0.06845735], [0.66338279, 0.70853238, 0.04624243, 0.07327316]]
i  431cc305-852a-4f31-90c8-63843c645fc2   row[0] [[0.25955544, 0.8518182999999999, 0.06741459, 0.10312672], [0.44515699999999997, 0.44129252, 0.10041215, 0.10764292]]
i  4335ec83-aba9-4a5e-8d1b-b165df488d7f   row[0] [[0.5072446700000001, 0.31438312, 0.1911716, 0.1952833]]
i  4365633e-2ffd-431b-ac57-232264f6bf9d   row[0] [[0.50202852, 0.46287409, 0.03958192, 0.05440814], [0.59767989, 0.65733738, 0.03609771, 0.05318234]]
i  43694f90-913b-41c9-926e-2880cb85983b   row[0] [[0.37844749, 0.28193514000000003, 0.07266664, 0.08011292]]
i  436fefbe-7b4e-4e5d-a83f-9a123ff39122   

...

i  e1197d32-2b28-4ca9-9e83-66a40fda1a3b   row[0] [[0.39997014000000003, 0.40710492, 0.23322458000000001, 0.30611011]]
i  e11fcdcd-b66d-4ad2-810e-4926680a53ae   row[0] [[0.38763596, 0.34798614, 0.17513473000000002, 0.21859348]]
i  e11fead2-7cc6-417e-ab74-8842f0fc925e   row[0] [[0.43020912, 0.40127963, 0.17295583, 0.15858716]]
i  e1233a70-101c-408f-8165-49c47c245f3f   row[0] [[0.29810941, 0.30261189, 0.09422102, 0.11844395]]
i  e12a5aa4-981a-4403-8eb6-f37fda419070   row[0] [[0.39182052, 0.4366037, 0.07950192, 0.0819158], [0.5372321800000001, 0.74647796, 0.06367715, 0.07814173]]
i  e132d2c8-aa54-4462-8ee9-6c514022fa51   row[0] [[0.40466614, 0.24951523, 0.09656841000000001, 0.14182396]]
i  e1333d5e-39b1-4a2e-89ed-317e286c289f   row[0] [[0.43994591, 0.26467964, 0.04845858, 0.12269387]]
i  e137276d-1b8b-4a9d-bba3-8d8fa4778be0   row[0] [[0.48174778, 0.36357551, 0.11379096, 0.13236117]]
i  e13981c7-acc5-4f00-876a-49a27e37457d   row[0] [[0.43334842, 0.38974831, 0.09326079999999999, 0.11643675]]

i  e8093653-ef96-4520-aa3c-a72ddba738b0   row[0] [[0.39655711, 0.17442515, 0.08009815, 0.11495032000000001]]
i  e80bb54d-6960-4dbe-a113-cc9a921c9985   row[0] [[0.45456856, 0.43199659999999995, 0.14609098, 0.23592952]]
i  e812a83b-a3b5-432c-8372-2d10ca39c76d   row[0] [[0.43496849, 0.4743078, 0.12440612000000001, 0.1532497]]
i  e8152ef2-182e-4145-8635-b6ceb34c6ce5   row[0] [[0.49228354, 0.7821448400000001, 0.03852163, 0.08400662]]
i  e81acd48-fdfe-49c3-9eab-1df9acbea689   row[0] [[0.44271105, 0.47298467, 0.09902903, 0.11608825]]
i  e8203458-24e7-4f33-8a2f-83a6f1953b9f   row[0] [[0.3959003, 0.47782661, 0.11411526, 0.14322476]]
i  e82b479b-9e6a-4cc7-af4f-ad4add38e68a   row[0] [[0.41051538, 0.70766958, 0.09602539, 0.12497012]]
i  e82f9992-b8c1-4d71-87a0-6b61b4a9434d   row[0] [[0.35798907, 0.17617929000000002, 0.22073395, 0.25492867]]
i  e837a2e0-27dc-4196-92e4-8f5d91812316   row[0] [[0.4585027, 0.18439739, 0.13342608, 0.14602822000000001]]
i  e83b8d6d-c3a7-4f37-9397-47b762582288   row[0] [[

i  ef5636d7-f207-4baf-ae5f-9bc5a9249141   row[0] [[0.47455368000000003, 0.33497391, 0.2032204, 0.25126183]]
i  ef609c47-f735-4e88-91dc-6737e60ed333   row[0] [[0.34637897, 0.49044751000000003, 0.09141319, 0.12481681]]
i  ef637933-6503-46e7-a122-4a63f41f19c0   row[0] [[0.4730159, 0.17513943, 0.10068013, 0.15118619]]
i  ef637a2d-4a36-4076-a97c-86ad2c45765a   row[0] [[0.14477518, 0.39012076, 0.30466209, 0.28572525]]
i  ef63cb8c-3892-42f4-8c6c-77a207c0089e   row[0] [[0.33886879999999997, 0.49206223, 0.06901017, 0.06062977]]
i  ef64b590-15be-42d6-99e0-aac48fe6ec9b   row[0] [[0.42356786, 0.34393639, 0.12536995, 0.12126953]]
i  ef654b51-79f7-4051-9081-a3b767a5926a   row[0] [[0.50447699, 0.25909469, 0.07746599, 0.08606539]]
i  ef667a1c-553a-49d5-a133-113fcc3501c5   row[0] [[0.50399793, 0.26202695, 0.06428865, 0.15007037]]
i  ef6e1d6f-3521-45a0-8939-8068d284b0b0   row[0] [[0.39896762, 0.47632779999999997, 0.18850117, 0.21346251]]
i  ef7735f3-91ea-47eb-b62c-2b07ac2d020a   row[0] [[0.4327488300000

i  f6918535-731d-4642-a2c3-cad148baee7f   row[0] [[0.40822951, 0.53627499, 0.09397525, 0.15759057]]
i  f6926c39-1e2f-408c-b930-fda17d9cc1da   row[0] [[0.50852086, 0.49665184, 0.09239845000000001, 0.20913231000000002]]
i  f692fb24-1e02-44a4-992d-b816056ce886   row[0] [[0.40054862, 0.6391283999999999, 0.13947742, 0.11759499]]
i  f6949076-9b61-4392-9ba0-b422cd07d488   row[0] [[0.42332957, 0.39962349, 0.12221098, 0.14311032]]
i  f699729a-649e-4e14-9a33-f90c18326110   row[0] [[0.53247437, 0.26647558, 0.1430103, 0.17958179]]
i  f69c0a60-08d9-4ab8-9ae9-04b1c2fdd213   row[0] [[0.52861005, 0.19446191000000002, 0.045646, 0.17187116]]
i  f6a6ec40-b0b1-4c2f-951b-14cb7aff77e1   row[0] [[0.54015631, 0.41321067, 0.06689546, 0.05028978]]
i  f6b6a029-c30e-4224-8cc1-48de06ff3640   row[0] [[0.40440193, 0.49466951000000003, 0.11949357000000001, 0.16292944]]
i  f6b794a6-8bf0-4771-bdc4-1410e8d21748   row[0] [[0.41303756, 0.30960901, 0.12293606, 0.13647102]]
i  f6bff9b2-bb8a-44f7-86be-1676c591ad67   row[0] [

i  fce1439f-36ca-4fa0-a572-30d0f660c023   row[0] [[0.41461622000000004, 0.44234659, 0.17796025000000001, 0.22445236000000002]]
i  fce23864-afaf-43e3-be63-b44250aba26a   row[0] [[0.36924221, 0.60517895, 0.055398420000000004, 0.06333391000000001], [0.48093866, 0.31418105, 0.05953291, 0.08555589]]
i  fcebc4dc-58d9-4ad4-a570-714695a60d5f   row[0] [[0.54523148, 0.40517226, 0.13598507, 0.41493021]]
i  fced8dfc-c816-45c4-be46-0c23684f72e5   row[0] [[0.43207192, 0.7069283, 0.069213, 0.08015378000000001]]
i  fcef3635-c141-4658-a715-80dfc841d40e   row[0] [[0.45482846, 0.44176765, 0.09208096, 0.09635103]]
i  fcf17344-4c86-4c75-8fd9-031bb545152f   row[0] [[0.58731616, 0.62835153, 0.06881266, 0.103085]]
i  fcf4edc3-ee48-4fa2-9965-309a64eb33fc   row[0] [[0.49704693, 0.3280907, 0.19096958, 0.24393375]]
i  fcfd61bb-9ddf-496d-9fdb-ac2b8cfbde4b   row[0] [[0.33315772, 0.45074049, 0.15088849000000001, 0.16002947]]
i  fcff5a38-3693-4623-bbb0-5cce0c23d0a4   row[0] [[0.39102372, 0.24510501, 0.13480754, 0.135

In [38]:
files = [f for f in os.listdir(mute_path) if f.endswith('.jpg')]
len(files)

1811

In [43]:
mute_data

bboxes  \
000b9a1b-d3a5-459f-8326-31235348b807  [[0.48372246, 0.51778145, 0.04780773, 0.105862...   
000d3f03-ca4b-44cc-8d8c-cdd12735e35b  [[0.30495339, 0.5748133400000001, 0.52472458, ...   
0018e992-f88e-4dd3-89c4-83d933e6b063  [[0.50047942, 0.61563948, 0.11658545000000001,...   
00283157-0fa8-4931-9ec1-a85ed9feac9b  [[0.43165491, 0.28045531, 0.03996719, 0.113830...   
002b2e3b-9d21-4921-a418-8435bc65fa59  [[0.44529762, 0.24427071, 0.1457059, 0.2161295...   
...                                                                                 ...   
ffe1214c-4cdb-4662-aeff-3cb6d9bbcf5c  [[0.45627985, 0.19176773, 0.09545147, 0.1324622]]   
ffe1b2c8-a5c6-406c-ba5b-6b15fb6306f3  [[0.40826623, 0.38899408, 0.14786205, 0.184966...   
ffec02aa-d1a1-48be-9a8c-4da968f5a7ef  [[0.41477847, 0.43058818, 0.28316482, 0.271577...   
ffeccd8b-8203-4b83-bc6f-e59185859ea0  [[0.40943279, 0.25550209, 0.07654883, 0.250987...   
fffd7f15-3c76-4bb3-8de7-01437d93dada  [[0.40165368, 0.25615628, 0.30457509, 0.3069493]]   

                                                  labels leading_hand  \
000b9a1b-d3a5-459f-8326-31235348b807  [mute, no_gesture]        right   
000d3f03-ca4b-44cc-8d8c-cdd12735e35b              [mute]        right   
0018e992-f88e-4dd3-89c4-83d933e6b063              [mute]        right   
00283157-0fa8-4931-9ec1-a85ed9feac9b  [mute, no_gesture]        right   
002b2e3b-9d21-4921-a418-8435bc65fa59  [mute, no_gesture]        right   
...                                                  ...          ...   
ffe1214c-4cdb-4662-aeff-3cb6d9bbcf5c              [mute]        right   
ffe1b2c8-a5c6-406c-ba5b-6b15fb6306f3              [mute]         left   
ffec02aa-d1a1-48be-9a8c-4da968f5a7ef              [mute]         left   
ffeccd8b-8203-4b83-bc6f-e59185859ea0              [mute]         left   
fffd7f15-3c76-4bb3-8de7-01437d93dada              [mute]        right   

                                     leading_conf  \
000b9a1b-d3a5-459f-8326-31235348b807            1   
000d3f03-ca4b-44cc-8d8c-cdd12735e35b            1   
0018e992-f88e-4dd3-89c4-83d933e6b063            1   
00283157-0fa8-4931-9ec1-a85ed9feac9b            1   
002b2e3b-9d21-4921-a418-8435bc65fa59            1   
...                                           ...   
ffe1214c-4cdb-4662-aeff-3cb6d9bbcf5c            1   
ffe1b2c8-a5c6-406c-ba5b-6b15fb6306f3            1   
ffec02aa-d1a1-48be-9a8c-4da968f5a7ef            1   
ffeccd8b-8203-4b83-bc6f-e59185859ea0            1   
fffd7f15-3c76-4bb3-8de7-01437d93dada            1   

                                                                                user_id  
000b9a1b-d3a5-459f-8326-31235348b807  77443178788d7a05ba0af7dc78167163a9ddda68c09658...  
000d3f03-ca4b-44cc-8d8c-cdd12735e35b  5beb90cf59482df367e1d4f9ab93518e7be4f8c63a50f5...  
0018e992-f88e-4dd3-89c4-83d933e6b063  c1b59340bc23985bd32c4a268bee5ff8d70c75b434f76a...  
00283157-0fa8-4931-9ec1-a85ed9feac9b  f880d44910f866441905ad78e8b61a15cdfd06552f8989...  
002b2e3b-9d21-4921-a418-8435bc65fa59  fb038674dc76f3bea11a051dabde0df08582bfdd3a8ad9...  
...                                                                                 ...  
ffe1214c-4cdb-4662-aeff-3cb6d9bbcf5c  35ad4a0746e7e1c04b78832cb64ea1547cf16d8c372015...  
ffe1b2c8-a5c6-406c-ba5b-6b15fb6306f3  81c043cdb97ba701cfdb1b789355602a6d5676227529d5...  
ffec02aa-d1a1-48be-9a8c-4da968f5a7ef  c1b59340bc23985bd32c4a268bee5ff8d70c75b434f76a...  
ffeccd8b-8203-4b83-bc6f-e59185859ea0  2452eb639d233b8132dc50cbeb419aa246a98b8d45cf60...  
fffd7f15-3c76-4bb3-8de7-01437d93dada  53077b819f7acc32945df2f854d8280e43f93930b4cd59...  

[28971 rows x 5 columns]

In [50]:
mute_files = os.listdir(mute_path)

file_index = 1000
for mute_file in mute_files:
    image_pth = mute_path+'/'+mute_file
    image = Image.open(image_pth).convert("RGB")
    mute_prefix = mute_file.split('.')[0]
    mute_index = mute_data[mute_prefix]['labels'].index('mute')
    bbox = mute_data[mute_prefix]['bboxes'][mute_index]  #[0.48372246, 0.51778145, 0.04780773, 0.10586212]
    x1, y1, w, h = bbox
    width, height = image.size

    bbox_abs = [x1 * width, y1 * height, (x1 + w) * width, (y1 + h) * height]
    im1 = image.crop(bbox_abs)
    #im1.show()
    im1 = im1.save("data/mute-processed/"+str(file_index)+".jpg") 
    file_index+=1

    #break


KeyboardInterrupt: 

In [11]:
os.mkdir('data/one-processed2')

In [19]:
file_index = 6000
rotate = True

for i ,row in one_df.iterrows():
    #print('i ',i,'  row[0]', row[0])
    image_pth = one_path+i+'.jpg'
    
    if not os.path.exists(image_pth): 
        continue
    image = Image.open(image_pth).convert("RGB")
    one_prefix = i #dislike_file.split('.')[0]
    one_index = row[1].index('one')
    bbox = row[0][one_index]  #[0.48372246, 0.51778145, 0.04780773, 0.10586212]
    x1, y1, w, h = bbox
    width, height = image.size
    bbox_abs = [x1 * width, y1 * height, (x1 + w) * width, (y1 + h) * height]
    im1 = image.crop(bbox_abs)
    if rotate:
        numbers = [90, 270]
        rotation_angle = random.choice(numbers)
        #print(rotation_angle)
        im1 = im1.rotate(rotation_angle, expand=True)
        rotate = False
    else:
        rotate = True

    #im1.show()
    #break
    im1 = im1.save("data/one-processed2/"+str(file_index)+".jpg") 
    file_index+=1
    if file_index > 7500: break

In [10]:
len(os.listdir('data/one-processed'))

1758

In [23]:
os.mkdir('data/none')

In [54]:
call_path = '/Users/jeyasri/Downloads/hagrid-sample-30k-384p/hagrid_30k/train_val_call/'

call_annotation_path = '/Users/jeyasri/Downloads/hagrid-sample-30k-384p/ann_train_val/call.json'

fist_path = '/Users/jeyasri/Downloads/hagrid-sample-30k-384p/hagrid_30k/train_val_fist/'

fist_annotation_path = '/Users/jeyasri/Downloads/hagrid-sample-30k-384p/ann_train_val/fist.json'

four_path = '/Users/jeyasri/Downloads/hagrid-sample-30k-384p/hagrid_30k/train_val_four/'

four_annotation_path = '/Users/jeyasri/Downloads/hagrid-sample-30k-384p/ann_train_val/four.json'

rock_path = '/Users/jeyasri/Downloads/hagrid-sample-30k-384p/hagrid_30k/train_val_rock/'

rock_annotation_path = '/Users/jeyasri/Downloads/hagrid-sample-30k-384p/ann_train_val/rock.json'

three_path = '/Users/jeyasri/Downloads/hagrid-sample-30k-384p/hagrid_30k/train_val_three/'

three_annotation_path = '/Users/jeyasri/Downloads/hagrid-sample-30k-384p/ann_train_val/three.json'

two_path = '/Users/jeyasri/Downloads/hagrid-sample-30k-384p/hagrid_30k/train_val_two_up/'

two_annotation_path = '/Users/jeyasri/Downloads/hagrid-sample-30k-384p/ann_train_val/two_up.json'


In [52]:
df = pd.read_json(two_annotation_path).transpose()
print(df.shape)
df.head()

(29679, 5)


bboxes  \
4b479511-704b-44f8-beeb-3b2213a8dd06  [[0.25340939, 0.90522063, 0.07370084, 0.068572...   
50b1d6a0-78ca-4726-88d8-5f425ded4b0b  [[0.24078039999999998, 0.31171353, 0.264768270...   
5d7445de-6d12-4eba-b4e9-c757b6c4cb54  [[0.22235418, 0.24312833, 0.17616603, 0.300937...   
d6018575-1b38-44cf-9945-87c6731bc1c1  [[0.72723033, 0.36515241, 0.1533959, 0.15454084]]   
dba6d732-0383-4b3c-800b-bf8b8b9851cd  [[0.24906428, 0.26580212000000003, 0.05331466,...   

                                                    labels leading_hand  \
4b479511-704b-44f8-beeb-3b2213a8dd06  [no_gesture, two_up]         left   
50b1d6a0-78ca-4726-88d8-5f425ded4b0b              [two_up]        right   
5d7445de-6d12-4eba-b4e9-c757b6c4cb54              [two_up]        right   
d6018575-1b38-44cf-9945-87c6731bc1c1              [two_up]         left   
dba6d732-0383-4b3c-800b-bf8b8b9851cd  [two_up, no_gesture]        right   

                                     leading_conf  \
4b479511-704b-44f8-beeb-3b2213a8dd06            1   
50b1d6a0-78ca-4726-88d8-5f425ded4b0b            1   
5d7445de-6d12-4eba-b4e9-c757b6c4cb54            1   
d6018575-1b38-44cf-9945-87c6731bc1c1            1   
dba6d732-0383-4b3c-800b-bf8b8b9851cd            1   

                                                                                user_id  
4b479511-704b-44f8-beeb-3b2213a8dd06  c8922c52e56b5bca2659a6849720fd6b36ff9d6e598c1e...  
50b1d6a0-78ca-4726-88d8-5f425ded4b0b  cd88f0a3ba23bba5feaee43e90345f58374853e1a826cd...  
5d7445de-6d12-4eba-b4e9-c757b6c4cb54  dadf1195045c05d74d264786dd3c5cad53baddceeeb6d7...  
d6018575-1b38-44cf-9945-87c6731bc1c1  2f7a11777bee041d9eafdd168a1593ffc854f356eaa3f2...  
dba6d732-0383-4b3c-800b-bf8b8b9851cd  5de423c55f56eaea795eeee9665d949328d901f3c968ea...

In [30]:
file_index = 1000

In [56]:
path = two_path
_LABEL = 'two_up'

files = os.listdir(path)
data = df
count = 0
for i ,row in df.iterrows():
    #print('i ',i,'  row[0]', row[0])
    image_pth = path+i+'.jpg'
    
    if not os.path.exists(image_pth): 
        continue
        
    image = Image.open(image_pth).convert("RGB")
    one_prefix = i #dislike_file.split('.')[0]
    print(row[1])
    one_index = row[1].index(_LABEL)
    print("one_index ",one_index)
    bbox = row[0][one_index]  #[0.48372246, 0.51778145, 0.04780773, 0.10586212]
    print("bbox ",bbox)
    x1, y1, w, h = bbox
    width, height = image.size
    bbox_abs = [x1 * width, y1 * height, (x1 + w) * width, (y1 + h) * height]
    im1 = image.crop(bbox_abs)

    #im1.show()
    #break
    im1 = im1.save("data/none/"+str(file_index)+".jpg") 
    file_index+=1
    print("file_index ",file_index)
    if file_index > 2500: break

print('count ',count)

['two_up', 'no_gesture']
one_index  0
bbox  [0.24906428, 0.26580212000000003, 0.05331466, 0.07476095]
file_index  2251
['no_gesture', 'two_up']
one_index  1
bbox  [0.45624619, 0.25511518, 0.22491846000000001, 0.22361492]
file_index  2252
['two_up', 'no_gesture']
one_index  0
bbox  [0.43003502, 0.38761028000000003, 0.07139377, 0.10731853]
file_index  2253
['two_up', 'no_gesture']
one_index  0
bbox  [0.44878993, 0.47663452, 0.05323775, 0.08929192]
file_index  2254
['no_gesture', 'two_up']
one_index  1
bbox  [0.47945679999999996, 0.48331687, 0.05285926, 0.16194454]
file_index  2255
['no_gesture', 'two_up']
one_index  1
bbox  [0.65720003, 0.42345636000000003, 0.07172243, 0.09887543]
file_index  2256
['two_up']
one_index  0
bbox  [0.095262, 0.28725554000000003, 0.15245913, 0.13355188]
file_index  2257
['no_gesture', 'two_up']
one_index  1
bbox  [0.57412247, 0.32008741, 0.08134189, 0.13079691000000002]
file_index  2258
['two_up', 'no_gesture']
one_index  0
bbox  [0.17253173, 0.17561587, 0.11

['two_up']
one_index  0
bbox  [0.6477283500000001, 0.26266877, 0.14532895, 0.23122199999999998]
file_index  2341
['two_up', 'no_gesture']
one_index  0
bbox  [0.20927592, 0.27166694, 0.0884856, 0.13191561000000002]
file_index  2342
['two_up']
one_index  0
bbox  [0.28278341, 0.34460451000000003, 0.15494646, 0.24356772000000002]
file_index  2343
['no_gesture', 'two_up']
one_index  1
bbox  [0.63231251, 0.16571675, 0.10822701, 0.20778265]
file_index  2344
['two_up']
one_index  0
bbox  [0.26205979, 0.35408202, 0.09560916, 0.16018922]
file_index  2345
['two_up']
one_index  0
bbox  [0.70574183, 0.23529664, 0.11504643, 0.28337818]
file_index  2346
['two_up', 'no_gesture']
one_index  0
bbox  [0.29496748, 0.4458775, 0.08362228000000001, 0.12084408]
file_index  2347
['no_gesture', 'two_up']
one_index  1
bbox  [0.6701607900000001, 0.27296822, 0.09175679, 0.13319703]
file_index  2348
['two_up']
one_index  0
bbox  [0.07441567, 0.20636155, 0.1709538, 0.25722275]
file_index  2349
['no_gesture', 'two_up

['no_gesture', 'two_up']
one_index  1
bbox  [0.62429095, 0.20475571, 0.13261667, 0.19899143]
file_index  2429
['two_up', 'no_gesture']
one_index  0
bbox  [0.33682548, 0.24224247000000002, 0.12830424, 0.15130516]
file_index  2430
['two_up']
one_index  0
bbox  [0.21335965, 0.40692186, 0.11488661, 0.16412369999999998]
file_index  2431
['two_up']
one_index  0
bbox  [0.66033191, 0.22772572, 0.20726287000000002, 0.27594443]
file_index  2432
['two_up']
one_index  0
bbox  [0.64891456, 0.47641725, 0.07242787, 0.17265975]
file_index  2433
['no_gesture', 'two_up']
one_index  1
bbox  [0.58739073, 0.40436503, 0.0850017, 0.12776889]
file_index  2434
['two_up']
one_index  0
bbox  [0.6287289500000001, 0.33496654, 0.13942603, 0.18097767]
file_index  2435
['no_gesture', 'two_up']
one_index  1
bbox  [0.7960192500000001, 0.23112975, 0.14774674000000002, 0.1687044]
file_index  2436
['no_gesture', 'two_up']
one_index  1
bbox  [0.53560136, 0.40533681, 0.06058193, 0.08347552]
file_index  2437
['two_up']
one_i

In [32]:
len(os.listdir('data/none/'))

251

# Processing all folders